In [2]:
import numpy as np
from matplotlib import pyplot as plt

import plotly.graph_objects as go
from plotly.subplots import make_subplots

from tigramite.causal_effects import CausalEffects

from sklearn.linear_model import LinearRegression
from sklearn.preprocessing import StandardScaler 

In [3]:
%cd /Users/alexandrine/Library/CloudStorage/OneDrive-TechnischeUniversitätBerlin/causal_detection_of_CSD/
import functions.generate_data as gendata
import functions.shift_detection as shiftdetect
import functions.sliding_windows as sw
import functions.indicators_computation as ind
import functions.significance_testing as sgtest

/Users/alexandrine/Library/CloudStorage/OneDrive-TechnischeUniversitätBerlin/causal_detection_of_CSD


# Fig. 1a,b

In [4]:
t_len = 10000

In [5]:
nb_surrogates = 1000

In [6]:
window_length = 1000
window_step = 1

# Base (Fig. 1a)

In [7]:
data = gendata.generate_time_series(t_len=t_len, model='base', sigma_Y=0.01, return_noise=True, bif_type='saddle-node', seed=5)['data']

In [8]:
deterministic_trend = gendata.generate_time_series(t_len=t_len, model='base', sigma_Y=0.0, return_noise=False, bif_type='saddle-node', seed=5)['data'][:,1]

In [12]:
bif_time = shiftdetect.find_shift_in_ts(data[:,1], lowwl=100, highwl = 3000, thresh=0.8, method='first') - 200

In [15]:
dataY = (data[:, 1] - deterministic_trend)[:bif_time]

In [16]:
time_windows, center_points = sw.get_centered_sliding_windows(window_length, window_step, t_len)
window_center_points_before_bif = [x for x in center_points if x <= (bif_time-window_length // 2)]

In [17]:
reg_autocorr = ind.regular_autocorrelation(data=dataY, time_windows=time_windows, lag=1, detrend=False)

In [18]:
graph =  np.array([[['', '-->']], #y
                   ], dtype='<U3')

X = [(0,-1)]
Y = [(0,0)]

causal_effects = CausalEffects(graph, graph_type='stationary_dag', X=X, Y=Y, S=None, 
                               hidden_variables=None, verbosity=0)

In [19]:
causalLinReg_base, _, _ = ind.pipeline_causalEE_weighted(
        causal_effects, dataY.reshape(-1,1), LinearRegression(), StandardScaler(),
        n_points=150, time_windows=time_windows, var_names=[r'$Y$'], detrend=False,
        )

In [21]:
%%capture

fig = make_subplots(rows=2, cols=1, row_heights=[0.2, 0.2], vertical_spacing=0.04)

len_bbif = len(window_center_points_before_bif)
x_values = [i for i in range(len_bbif)]

fig.add_trace(go.Scatter(x=[i for i in range(len(data[:, 1]))], y=data[:, 1], mode='lines', line=dict(color='rgba(128, 128, 128, 1)'), name='Stochastic', legendgroup='1'), row=1, col=1)
fig.add_trace(go.Scatter(x=[i for i in range(len(data[:, 1]))], y=deterministic_trend, mode='lines', line=dict(color='rgba(0, 0, 0, 0.6)'), name='Deterministic', legendgroup='1'), row=1, col=1)

fig.add_trace(go.Scatter(x=list(window_center_points_before_bif), y=reg_autocorr[500:(500+len_bbif)], mode='lines', name='AC1', line=dict(color='orange', width=3), opacity=1, legendgroup='2'), row=2, col=1)
slope, intercept = np.polyfit(x_values, reg_autocorr[:len_bbif], 1)
pv, _ = sgtest.p_value_from_fourier(reg_autocorr[:len_bbif], nb_surrogates, slope)
if pv < 0.001:
    fig.add_trace(go.Scatter(x=list(window_center_points_before_bif), y=slope*center_points + intercept, mode='lines', name=f'p < 0.001', line=dict(color='orange', width=3, dash="dot"), legendgroup='2'), row=2, col=1)
else:
    fig.add_trace(go.Scatter(x=list(window_center_points_before_bif), y=slope*center_points + intercept, mode='lines', name=f'p = {pv:.3f}', line=dict(color='orange', width=3, dash="dot"), legendgroup='2'), row=2, col=1)


fig.add_trace(go.Scatter(x=list(window_center_points_before_bif), y=causalLinReg_base[500:(500+len_bbif)], mode='lines', name='DCE', line=dict(color='#00AAD4', width=3), opacity=0.7, legendgroup='2'), row=2, col=1)
slope, intercept = np.polyfit(x_values, causalLinReg_base[:len_bbif], 1)
pv, _ = sgtest.p_value_from_fourier(causalLinReg_base[:len_bbif], nb_surrogates, slope)
if pv < 0.001:
    fig.add_trace(go.Scatter(x=list(window_center_points_before_bif), y=slope*center_points + intercept, mode='lines', name=f'p < 0.001', line=dict(color='#00AAD4', width=3, dash="dot"), opacity=0.7, legendgroup='2'), row=2, col=1)
else:
    fig.add_trace(go.Scatter(x=list(window_center_points_before_bif), y=slope*center_points + intercept, mode='lines', name=f'p = {pv:.3f}', line=dict(color='#00AAD4', width=3, dash="dot"), opacity=0.7, legendgroup='2'), row=2, col=1)


maximum = max(reg_autocorr[:len_bbif])
minimum = min(reg_autocorr[:len_bbif])

fig.add_shape(type="line", x0=bif_time, y0=min(data[:, 1])-1, x1=bif_time, y1=max(data[:, 1])+1, line=dict(color='rgba(204, 204, 204, 1)', width=2, dash="dashdot"), row=1, col=1)
fig.add_shape(type="line", x0=bif_time, y0=minimum-0.5, x1=bif_time, y1=maximum+0.5, line=dict(color='rgba(204, 204, 204, 1)', width=2, dash="dashdot"), row=2, col=1)

In [ ]:
fig.update_layout(paper_bgcolor='rgba(0, 0, 0, 0)',  # entire plot background
    plot_bgcolor='rgba(215, 238, 244, 0.3)',    # plotting area
    height=550, width=600, xaxis1=dict(range=[0, 9000], showticklabels=False), 
    xaxis2=dict(range=[0, 9000], title='Time', 
                tickvals=[0, 2000, 4000, 6000, 8000, 10000], ticktext=['0', '2,000', '4,000', '6,000', '8,000', '10,000']), 
    yaxis1_title = 'State of 𝑌', yaxis2_title = 'CSD indicators',
                      yaxis1_range=[-1.5, 1.7], yaxis2_range=[0.93, 1.01],
                      #legend_tracegroupgap = 200,
                    legend=dict(  # Position the global legend outside of the plotting area
        x=1.02,
        y=-0.02,
        tracegroupgap=105,
    ))

fig.update_annotations()

In [23]:
# fig.write_image("fig1_noconfounder.svg")

# False alarm (Fig. 1b)

In [24]:
data = gendata.generate_time_series(t_len, sigma_Y = 0.01, sigma_X=0.5, seed = 6, model = 'falseAlarm', return_noise=True, X_power = 1, gamma=1, bif_type='saddle-node')

In [25]:
data_r = data['data'][:, 0]
data_X = data['data'][:, 1]
data_Y = data['data'][:, 2]

In [26]:
time_windows, center_points = sw.get_centered_sliding_windows(window_length, window_step, t_len)

In [27]:
reg_autocorr = ind.regular_autocorrelation(data=data_Y, time_windows=time_windows, lag=1, detrend=True)

In [28]:
graph =  np.array([[['', '-->'], ['', '-->']], #r residuals
                   [['', ''], ['', '-->']], #y
                   ], dtype='<U3')

X = [(1,-1)]
Y = [(1,0)]

causal_effects = CausalEffects(graph, graph_type='stationary_dag', X=X, Y=Y, S=None, 
                               hidden_variables=None, verbosity=0)

In [29]:
data_pair = np.hstack([data_X.reshape(-1, 1), data_Y.reshape(-1, 1)])

In [30]:
causalLinReg_falseAlarm, _, _ = ind.pipeline_causalEE_weighted(
        causal_effects, data_pair, LinearRegression(), StandardScaler(),
        n_points=150, time_windows=time_windows, var_names=[r'$X$', r'$Y$'], detrend=False,
        )

In [31]:
#%%capture

fig = make_subplots(rows=3, cols=1, row_heights=[0.2, 0.2, 0.2], vertical_spacing=0.04)

fig.add_trace(go.Scatter(x=[i for i in range(len(data_Y))], y=data['data'][:, 1], mode='lines', line=dict(color='#DE8787'), name='Simulated confounder', legendgroup='1'), row=1, col=1)
fig.add_trace(go.Scatter(x=[i for i in range(len(data_Y))], y=data_Y, mode='lines', line=dict(color='rgba(128, 128, 128, 1)'), name='Simulated tipping system', legendgroup='2'), row=2, col=1)

fig.add_trace(go.Scatter(x=list(center_points), y=reg_autocorr[500:9500], mode='lines', name='AC1', line=dict(color='orange', width=3), legendgroup='3'), row=3, col=1)

slope, intercept = np.polyfit(center_points, reg_autocorr, 1)
pv, _ = sgtest.p_value_from_fourier(reg_autocorr, nb_surrogates, slope)
if pv < 0.001:
    fig.add_trace(go.Scatter(x=list(center_points), y=slope*center_points + intercept, mode='lines', name=f'p < 0.001', line=dict(color='orange', width=3, dash="dot"), legendgroup='3'), row=3, col=1)
else:
    fig.add_trace(go.Scatter(x=list(center_points), y=slope*center_points + intercept, mode='lines', name=f'p = {pv:.3f}', line=dict(color='orange', width=3, dash="dot"), legendgroup='3'), row=3, col=1)


fig.add_trace(go.Scatter(x=list(center_points), y=causalLinReg_falseAlarm, mode='lines', name='DCE', line=dict(color='#00AAD4', width=3), opacity=1, legendgroup='3'), row=3, col=1)
slope, intercept = np.polyfit(center_points, causalLinReg_falseAlarm, 1)
pv, _ = sgtest.p_value_from_fourier(causalLinReg_falseAlarm, nb_surrogates, slope)
if pv < 0.001:
    fig.add_trace(go.Scatter(x=list(center_points), y=slope*center_points + intercept, mode='lines', name=f'p < 0.001', line=dict(color='#00AAD4', width=3, dash="dot"), opacity=1, legendgroup='3'), row=3, col=1)
else:
    fig.add_trace(go.Scatter(x=list(center_points), y=slope*center_points + intercept, mode='lines', name=f'p = {pv:.3f}', line=dict(color='#00AAD4', width=3, dash="dot"), opacity=1, legendgroup='3'), row=3, col=1)

In [ ]:
fig.update_layout(paper_bgcolor='rgba(0, 0, 0, 0)',  # entire plot background
    plot_bgcolor='rgba(215, 238, 244, 0.3)',    # plotting area
    height=700, width=600, xaxis1=dict(range=[0, 10000], showticklabels=False), xaxis2=dict(range=[0, 10000], showticklabels=False), 
    xaxis3=dict(range=[0, 10000], title='Time', 
                tickvals=[0, 2000, 4000, 6000, 8000, 10000], ticktext=['0', '2,000', '4,000', '6,000', '8,000', '10,000']), 
    yaxis1_title = 'State of 𝑋', yaxis2_title = 'State of 𝑌', yaxis3_title = 'CSD indicators',
                      yaxis1_range=[-5, 3.5], 
                      yaxis2_range=[0.9, 1.7], 
                      yaxis3_range=[0.915, 1.005],
                    legend=dict(
        x=1.02,
        y=0.01,
        tracegroupgap=150,
    ))

fig.update_annotations()

In [33]:
# fig.write_image("fig1_falseAlarm.svg")

# Confounder decreasing autocorrelation (Fig. 1b)

In [36]:
data = gendata.generate_time_series(t_len, sigma_Y = 0.01, sigma_X=1, seed = 0, model = 'confounderDecreasAC', return_noise=False, X_power = 1, gamma=1, bif_type='saddle-node')

In [37]:
data_r = data['data'][:, 0]
data_X = data['data'][:, 1]
data_Y = data['data'][:, 2]

In [48]:
bif_time = 7200

In [49]:
bif_time = bif_time
print(bif_time)

7200


In [50]:
time_windows, center_points = sw.get_centered_sliding_windows(window_length, window_step, t_len)
window_center_points_before_bif = [x for x in center_points if x <= (bif_time-window_length // 2)]

In [51]:
dataY = (data_Y - deterministic_trend)[:bif_time]
dataX = data_X[:bif_time]

In [52]:
reg_autocorr = ind.regular_autocorrelation(data=dataY, time_windows=time_windows, lag=1, detrend=True)

In [53]:
graph =  np.array([[['', '-->'], ['', '-->']], #r residuals
                   [['', ''], ['', '-->']], #y
                   ], dtype='<U3')

X = [(1,-1)]
Y = [(1,0)]

causal_effects = CausalEffects(graph, graph_type='stationary_dag', X=X, Y=Y, S=None, 
                               hidden_variables=None, verbosity=0)

In [54]:
data_pair = np.hstack([dataX.reshape(-1, 1), dataY.reshape(-1, 1)])

In [55]:
causalLinReg_DecreaseAC, _, _ = ind.pipeline_causalEE_weighted(
        causal_effects, data_pair, LinearRegression(), StandardScaler(),
        n_points=150, time_windows=time_windows, var_names=[r'$X$', r'$Y$'], detrend=True,
        )

In [56]:
%%capture

fig = make_subplots(rows=3, cols=1, row_heights=[0.2, 0.2, 0.2], vertical_spacing=0.04)

len_bbif = len(window_center_points_before_bif)
x_values = [i for i in range(len_bbif)]

fig.add_trace(go.Scatter(x=[i for i in range(len(data_Y))], y=data['data'][:, 1], mode='lines', line=dict(color='#DE8787'), name='Simulated confounder', legendgroup='1'), row=1, col=1)

fig.add_trace(go.Scatter(x=[i for i in range(len(data_Y))], y=data_Y, mode='lines', line=dict(color='rgba(128, 128, 128, 1)'), name='Simulated tipping system', legendgroup='2'), row=2, col=1)
fig.add_trace(go.Scatter(x=[i for i in range(len(data_Y))], y=deterministic_trend, mode='lines', line=dict(color='rgba(0, 0, 0, 0.6)'), name='Deterministic', legendgroup='2'), row=2, col=1)


fig.add_trace(go.Scatter(x=list(window_center_points_before_bif), y=reg_autocorr[500:(500+len_bbif)], mode='lines', name='AC1', line=dict(color='orange', width=3), legendgroup='3'), row=3, col=1)
slope, intercept = np.polyfit(x_values, reg_autocorr[:len_bbif], 1)
pv, _ = sgtest.p_value_from_fourier(reg_autocorr[:len_bbif], nb_surrogates, slope)
fig.add_trace(go.Scatter(x=list(window_center_points_before_bif), y=slope*center_points + intercept, mode='lines', name=f'p = {pv:.3f}', line=dict(color='orange', width=3, dash="dot"), legendgroup='3'), row=3, col=1)

fig.add_trace(go.Scatter(x=list(window_center_points_before_bif), y=causalLinReg_DecreaseAC, mode='lines', name='DCE', line=dict(color='#00AAD4', width=3), opacity=1, legendgroup='3'), row=3, col=1)
slope, intercept = np.polyfit(window_center_points_before_bif, causalLinReg_DecreaseAC, 1)

pv, _ = sgtest.p_value_from_fourier(causalLinReg_DecreaseAC, nb_surrogates, slope)
if pv < 0.001:
    fig.add_trace(go.Scatter(x=list(window_center_points_before_bif), y=slope*np.array(window_center_points_before_bif) + intercept, mode='lines', name=f'p < 0.001', line=dict(color='#00AAD4', width=3, dash="dot"), opacity=1, legendgroup='3'), row=3, col=1)
else:
    fig.add_trace(go.Scatter(x=list(window_center_points_before_bif), y=slope*np.array(window_center_points_before_bif) + intercept, mode='lines', name=f'p = {pv:.3f}', line=dict(color='#00AAD4', width=3, dash="dot"), opacity=1, legendgroup='3'), row=3, col=1)

maximum = max(reg_autocorr[:len_bbif])
minimum = min(reg_autocorr[:len_bbif])

fig.add_shape(type="line", x0=bif_time, y0=min(data_Y)-1, x1=bif_time, y1=max(data_Y)+1, line=dict(color='rgba(204, 204, 204, 1)', width=2, dash="dashdot"), row=2, col=1)
fig.add_shape(type="line", x0=bif_time, y0=minimum-0.5, x1=bif_time, y1=maximum+0.5, line=dict(color='rgba(204, 204, 204, 1)', width=2, dash="dashdot"), row=3, col=1)

In [57]:
fig.update_layout(paper_bgcolor='rgba(0, 0, 0, 0)',  # entire plot background
    plot_bgcolor='rgba(215, 238, 244, 0.3)',    # plotting area
    height=700, width=600, xaxis1=dict(range=[0, 9000], showticklabels=False), xaxis2=dict(range=[0, 9000], showticklabels=False), 
    xaxis3=dict(range=[0, 9000], title='Time', 
                tickvals=[0, 2000, 4000, 6000, 8000, 10000], ticktext=['0', '2,000', '4,000', '6,000', '8,000', '10,000']), 
    yaxis1_title = 'State of 𝑋', yaxis2_title = 'State of 𝑌', yaxis3_title = 'CSD indicators',
                      yaxis1_range=[-9, 6], yaxis2_range=[-1.5, 2], yaxis3_range=[0.95, 1.005],
                      #legend_tracegroupgap = 200,
                    legend=dict(  # Position the global legend outside of the plotting area
        x=1.02,
        y=0.01,
        tracegroupgap=150,
    ))

fig.update_annotations()

In [ ]:
# fig.write_image("fig1_falseNegative.svg")